In [68]:
import pandas as pd
import numpy as np
from sklearn.metrics import accuracy_score
import dask.dataframe as dd
import xgboost
from sklearn.preprocessing import MultiLabelBinarizer, LabelEncoder
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from xgboost import XGBClassifier,  XGBRanker

## Recipes dataset 

In [ ]:
df = pd.read_json("/home/german/Desktop/insight/data_challenge/datachallengeweek6/recipies.json")

In [ ]:
df["cuisine"].nunique()

## Build an co ocurrence matrix 

In [ ]:
df

In [ ]:
s = df["ingredients"]

mlb = MultiLabelBinarizer()

df_ = pd.DataFrame(mlb.fit_transform(s),columns=mlb.classes_, index=df.index)


In [ ]:
df_.head()



In [ ]:
data = df.join(df_, how='outer')
del df
del df_

In [ ]:
data.shape

In [ ]:
le = LabelEncoder()

In [ ]:
le.fit(data['cuisine'])

In [ ]:
list(le.classes_)

In [ ]:
len(le.classes_)

In [ ]:
le.transform(data['cuisine'])

## Labes encoding (20 of them )

In [ ]:
data["cuisine"] = le.transform(data['cuisine'])

In [ ]:
data

In [ ]:
del data["id"]

In [ ]:
del data["ingredients"]

In [ ]:
data.head()

In [ ]:
data = data.astype(np.int16)

## check for memory and store on drive matrix 

In [ ]:
data.head()

In [ ]:
data.info()

In [ ]:
data.to_csv("data_ready.csv")


# restart here 

In [45]:
data = pd.read_csv("data_ready.csv", low_memory=True, dtype=np.int16, index_col=0)

In [46]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 39774 entries, 0 to -25763
Columns: 6715 entries, cuisine to zucchini blossoms
dtypes: int16(6715)
memory usage: 509.7 MB


In [ ]:
#data_ = data.astype(np.int16)

In [ ]:
#del data

In [ ]:
#data_.info(memory_usage='deep')

In [47]:
data.head()

cuisine  (    oz.) tomato sauce  (   oz.) tomato paste  \
0        6                       0                      0   
1       16                       0                      0   
2        4                       0                      0   
3        7                       0                      0   
4        7                       0                      0   

   (10 oz.) frozen chopped spinach  \
0                                0   
1                                0   
2                                0   
3                                0   
4                                0   

   (10 oz.) frozen chopped spinach, thawed and squeezed dry  \
0                                                  0          
1                                                  0          
2                                                  0          
3                                                  0          
4                                                  0          

   (14 oz.) sweetened condensed milk  (14.5 oz.) diced tomatoes  \
0                                  0                          0   
1                                  0                          0   
2                                  0                          0   
3                                  0                          0   
4                                  0                          0   

   (15 oz.) refried beans  1% low-fat buttermilk  1% low-fat chocolate milk  \
0                       0                      0                          0   
1                       0                      0                          0   
2                       0                      0                          0   
3                       0                      0                          0   
4                       0                      0                          0   

         ...          yukon gold potatoes  yuzu  yuzu juice  za'atar  zest  \
0        ...                            0     0           0        0     0   
1        ...                            0     0           0        0     0   
2        ...                            0     0           0        0     0   
3        ...                            0     0           0        0     0   
4        ...                            0     0           0        0     0   

   zesty italian dressing  zinfandel  ziti  zucchini  zucchini blossoms  
0                       0          0     0         0                  0  
1                       0          0     0         0                  0  
2                       0          0     0         0                  0  
3                       0          0     0         0                  0  
4                       0          0     0         0                  0  

[5 rows x 6715 columns]

In [48]:
data.shape

(39774, 6715)

In [6]:
data_ = data[:20000]
del data

In [50]:
y_train = data["cuisine"]

In [51]:
del data["cuisine"]

In [52]:
X_train, X_test, y_train, y_test  = train_test_split(data, y_train, test_size=0.2, random_state=123)
del data

In [53]:
X_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 31819 entries, 22321 to 15725
Columns: 6714 entries, (    oz.) tomato sauce to zucchini blossoms
dtypes: int16(6714)
memory usage: 407.7 MB


In [54]:
y_train.head()

22321     3
2758     13
23666     9
9483     18
32137    13
Name: cuisine, dtype: int16

## Applying Kernel PCA 

In [63]:
from sklearn.decomposition import PCA, KernelPCA, SparsePCA, NMF

In [24]:
# Applying PCA

#pca = PCA(n_components = 300)
pca = PCA(n_components = 100)

Xtrain = pca.fit_transform(X_train)

In [25]:
Xtest = pca.transform(X_test)

## KERNEL PCA 

In [28]:
# Applying kERNEL PCA
from sklearn.decomposition import PCA, KernelPCA
#pca = PCA(n_components = 300)
kpca = KernelPCA(n_components = 100, kernel="rbf", gamma=10)

Xtrain = kpca.fit_transform(X_train)
                            #



In [29]:
Xtest = kpca.transform(X_test)

## Non negative matrix NMF

In [64]:
#spca = SparsePCA(n_components=100, normalize_components=True, random_state=0)
NMF = NMF(n_components=200, init='random', random_state=0)
Xtrain = NMF.fit_transform(X_train) 

In [65]:
Xtest = NMF.transform(X_test)

In [34]:
explained_variance = pca.explained_variance_ratio_

## XGBOOST

In [66]:
# fit model no training data
model = XGBClassifier(n_jobs=8, max_depth=7, n_estimators=500, min_child_weight= 8,)
model.fit(Xtrain, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=1, gamma=0, learning_rate=0.1, max_delta_step=0,
       max_depth=7, min_child_weight=8, missing=None, n_estimators=500,
       n_jobs=8, nthread=None, objective='multi:softprob', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1)

In [67]:
# make predictions for test data
y_pred = model.predict(Xtest)
predictions = [round(value) for value in y_pred]
# evaluate predictions
accuracy = accuracy_score(y_test, predictions)
print("Accuracy: %.2f%%" % (accuracy * 100.0))

Accuracy: 74.96%


## half data kpca + xgboost 20.35% accu
## half data pca + xgboost 62.82% accu, 68% complete
## half data NMF + xgboost 69.73%
## full data NMF + xgboost 74.96%

In [69]:
# create a train/test split
xgb_train = xgboost.DMatrix(Xtrain, label=y_train)
xgb_test = xgboost.DMatrix(Xtest, label=y_test)

In [ ]:
xgb_full = xgboost.DMatrix(X, label=y)


In [75]:
params = {
    
        "learning_rate":0.1, 
       "max_depth":7, "min_child_weight":8, "n_estimators":500,
        "objective":'multi:softprob', "num_class":20
       
}

In [ ]:
model_train = xgboost.train(params, xgb_train,  10000, evals = [(xgb_test, "test")], verbose_eval=600)


[07:56:53] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 44 extra nodes, 0 pruned nodes, max_depth=7
[07:56:53] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 78 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 62 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 62 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 54 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 72 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 62 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 30 extra nodes, 0 pruned nodes, max_depth=7
[07:56:54] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 40 extra nodes, 0 pruned nodes, max_

[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 112 extra nodes, 0 pruned nodes, max_depth=7
[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 78 extra nodes, 0 pruned nodes, max_depth=7
[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 90 extra nodes, 0 pruned nodes, max_depth=7
[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 64 extra nodes, 0 pruned nodes, max_depth=7
[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 46 extra nodes, 0 pruned nodes, max_depth=7
[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 82 extra nodes, 0 pruned nodes, max_depth=7
[07:56:58] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 68 extra nodes, 0 pruned nodes, max_depth=7
[07:56:59] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=7
[07:56:59] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 78 extra nodes, 0 pruned nodes, ma

[07:57:03] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 60 extra nodes, 0 pruned nodes, max_depth=7
[07:57:03] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 86 extra nodes, 0 pruned nodes, max_depth=7
[07:57:03] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 88 extra nodes, 0 pruned nodes, max_depth=7
[07:57:03] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=7
[07:57:04] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 80 extra nodes, 0 pruned nodes, max_depth=7
[07:57:04] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 60 extra nodes, 0 pruned nodes, max_depth=7
[07:57:04] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned nodes, max_depth=7
[07:57:04] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=7
[07:57:04] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 98 extra nodes, 0 pruned nodes, m

[07:57:10] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 100 extra nodes, 0 pruned nodes, max_depth=7
[07:57:10] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 78 extra nodes, 0 pruned nodes, max_depth=7
[07:57:10] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=7
[07:57:11] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 94 extra nodes, 0 pruned nodes, max_depth=7
[07:57:11] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 94 extra nodes, 0 pruned nodes, max_depth=7
[07:57:11] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 76 extra nodes, 0 pruned nodes, max_depth=7
[07:57:11] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=7
[07:57:11] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 58 extra nodes, 0 pruned nodes, max_depth=7
[07:57:11] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 92 extra nodes, 0 pruned nodes, m

[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 96 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 100 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 72 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 82 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 96 extra nodes, 0 pruned nodes, max_depth=7
[07:57:19] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 114 extra nodes, 0 pruned nodes, max_depth=7
[07:57:20] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 72 extra nodes, 0 pruned nodes, 

...

[10:19:24] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_depth=3
[10:19:24] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 14 extra nodes, 0 pruned nodes, max_depth=7
[10:19:24] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 12 extra nodes, 0 pruned nodes, max_depth=6
[10:19:24] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 12 extra nodes, 0 pruned nodes, max_depth=6
[10:19:24] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=4
[10:19:25] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 20 extra nodes, 0 pruned nodes, max_depth=7
[10:19:25] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=4
[10:19:25] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 14 extra nodes, 0 pruned nodes, max_depth=7
[10:19:25] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_d

[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 18 extra nodes, 0 pruned nodes, max_depth=7
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 14 extra nodes, 0 pruned nodes, max_depth=7
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 8 extra nodes, 0 pruned nodes, max_depth=4
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_depth=3
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 4 extra nodes, 0 pruned nodes, max_depth=2
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 12 extra nodes, 0 pruned nodes, max_depth=5
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=5
[10:19:29] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 16 extra nodes, 0 pruned nodes, max_depth=7
[10:19:30] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 8 extra nodes, 0 pruned nodes, max_dept

[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 12 extra nodes, 0 pruned nodes, max_depth=6
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 4 extra nodes, 0 pruned nodes, max_depth=2
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 14 extra nodes, 0 pruned nodes, max_depth=7
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 4 extra nodes, 0 pruned nodes, max_depth=2
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 8 extra nodes, 0 pruned nodes, max_depth=4
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 32 extra nodes, 0 pruned nodes, max_depth=7
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 14 extra nodes, 0 pruned nodes, max_depth=6
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 8 extra nodes, 0 pruned nodes, max_depth=4
[10:19:34] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_depth

[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 14 extra nodes, 0 pruned nodes, max_depth=7
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=5
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 30 extra nodes, 0 pruned nodes, max_depth=7
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_depth=3
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 12 extra nodes, 0 pruned nodes, max_depth=6
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_depth=3
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 16 extra nodes, 0 pruned nodes, max_depth=7
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 4 extra nodes, 0 pruned nodes, max_depth=2
[10:19:39] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_dept

[10:19:44] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 16 extra nodes, 0 pruned nodes, max_depth=7
[10:19:44] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=4
[10:19:44] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 24 extra nodes, 0 pruned nodes, max_depth=7
[10:19:44] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=5
[10:19:45] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 12 extra nodes, 0 pruned nodes, max_depth=6
[10:19:45] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_depth=5
[10:19:46] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 24 extra nodes, 0 pruned nodes, max_depth=7
[10:19:46] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 6 extra nodes, 0 pruned nodes, max_depth=3
[10:19:47] src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 10 extra nodes, 0 pruned nodes, max_d

In [77]:
shap_values = shap.TreeExplainer(model).shap_values(X)


NameError: name 'shap' is not defined